<a href="https://colab.research.google.com/github/ArtemMusienko/Voice-Assistant-with-TTS/blob/main/Voice_Assistant_with_TTS_Text_to_Speech.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Решение задачи:

Установим и импортируем необходимый ряд библиотек:

In [1]:
%%capture
!apt-get update -qq && apt-get install -y ffmpeg

# Полная очистка всех конфликтующих пакетов (самый надёжный способ)
!pip uninstall -y numpy transformers -q

# Устанавливаем чистый NumPy 1.26.4 БЕЗ зависимостей
!pip install "numpy==1.26.4" --force-reinstall --no-deps -q

# Теперь transformers 4.45.2 (работает идеально с Whisper large-v3)
!pip install "transformers==4.45.2" --force-reinstall -q

# Остальные пакеты
!pip install torch torchvision torchaudio torchcodec --extra-index-url https://download.pytorch.org/whl/cu118 -q
!pip install pydub bitsandbytes accelerate -q

print("✅ Установка завершена! Теперь нажми Runtime → Restart session")

In [2]:
import torch
import torchaudio
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, pipeline
from pydub import AudioSegment
from IPython.display import Audio, display, Javascript
from google.colab import output
from base64 import b64decode
import time
import re
import warnings
warnings.filterwarnings("ignore")

/usr/local/lib/python3.12/dist-packages/pydub/utils.py:300: SyntaxWarning: invalid escape sequence '\('
  m = re.match('([su]([0-9]{1,2})p?) \(([0-9]{1,2}) bit\)$', token)
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:301: SyntaxWarning: invalid escape sequence '\('
  m2 = re.match('([su]([0-9]{1,2})p?)( \(default\))?$', token)
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:310: SyntaxWarning: invalid escape sequence '\('
  elif re.match('(flt)p?( \(default\))?$', token):
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:314: SyntaxWarning: invalid escape sequence '\('
  elif re.match('(dbl)p?( \(default\))?$', token):


Эта часть кода — чистый **JavaScript**, который сохраняется в **Python**-переменную `RECORD_JS` как многострочная строка. Он нужен для того, чтобы в браузере (в **Google Colab**) записать звук с микрофона пользователя и вернуть его в **Python**-код в виде **base64-строки**:

In [3]:
RECORD_JS = """
const sleep = time => new Promise(resolve => setTimeout(resolve, time))
const b2text = blob => new Promise(resolve => {
  const reader = new FileReader()
  reader.onloadend = e => resolve(e.srcElement.result)
  reader.readAsDataURL(blob)
})
var record = time => new Promise(async resolve => {
  stream = await navigator.mediaDevices.getUserMedia({ audio: true })
  recorder = new MediaRecorder(stream)
  chunks = []
  recorder.ondataavailable = e => chunks.push(e.data)
  recorder.start()
  await sleep(time)
  recorder.onstop = async () => {
    blob = new Blob(chunks)
    text = await b2text(blob)
    resolve(text)
  }
  recorder.stop()
})
"""

Функция `record_audio` позволяет записывать голос пользователя прямо в **Google Colab** без каких-либо внешних библиотек или серверов.
Она запускает заранее подготовленный **JavaScript**-код в браузере, который получает доступ к микрофону, записывает ровно заданное количество секунд, превращает запись в **base64**-строку и возвращает её в **Python**.
Далее **Python** декодирует **base64**, добавляет недостающий паддинг (если нужно) и сохраняет результат как обычный **WAV-файл** «audio.wav», который потом можно подать в **Whisper** или любую другую модель распознавания речи:

In [4]:
def record_audio(seconds=8):
    """
    Записывает звук с микрофона пользователя в Google Colab.
    Возвращает путь к сохранённому файлу audio.wav.
    """
    # Внедряем JavaScript-код в страницу Colab, чтобы он стал доступен в браузере
    display(Javascript(RECORD_JS))

    # Вызываем функцию record(8000) из JavaScript и получаем результат
    data = output.eval_js('record(%d)' % (seconds * 1000))

    # Отделяем полезную base64-часть от префикса "data:audio/...;base64,"
    binary_data = data.split(',')[1]

    # Base64 требует, чтобы длина была кратна 4. Если не хватает — добавляем паддинг "="
    missing_padding = len(binary_data) % 4
    if missing_padding:
        binary_data += '=' * (4 - missing_padding)

    # Декодируем base64 в бинарные данные (bytes)
    binary = b64decode(binary_data)

    # Сохраняем бинарные данные в файл audio.wav
    audio_path = "audio.wav"
    with open(audio_path, "wb") as f:
        f.write(binary)

    # Возвращаем путь к файлу для дальнейшего использования (например, Whisper)
    return audio_path

Эта строка кода загружает и инициализирует мощнейшую модель `Whisper large-v3` для распознавания речи, которая будет превращать записанный аудиофайл в текст с высочайшей точностью.

In [5]:
# Создаём пайплайн для автоматического распознавания речи (Speech-to-Text)
transcriber = pipeline(
    "automatic-speech-recognition",          # Тип задачи — распознавание речи
    model="openai/whisper-large-v3",
    torch_dtype=torch.float16,               # Используем половинную точность (float16) — экономит видеопамять и ускоряет работу на GPU
    device_map="auto"                        # Автоматически распределяет модель по доступным устройствам (GPU + CPU если нужно)
)

config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/3.09G [00:00<?, ?B/s]

generation_config.json: 0.00B [00:00, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

...

merges.txt: 0.00B [00:00, ?B/s]

normalizer.json: 0.00B [00:00, ?B/s]

added_tokens.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

preprocessor_config.json:   0%|          | 0.00/340 [00:00<?, ?B/s]

Эти строки задают использование **LLM** — **Saiga Llama-3-8B** — и настраивают сверхэффективную 4-битную квантизацию:

In [6]:
model_name = "IlyaGusev/saiga_llama3_8b"

# Настраиваем 4-битную квантизацию через библиотеку bitsandbytes
# Это позволяет запустить 8-миллиардную модель даже на Colab с GPU T4 (16 ГБ VRAM)
quantization_config = BitsAndBytesConfig(
    load_in_4bit=True,                      # Включаем 4-битный режим (вместо 16-бит → экономия памяти в ~4 раза)
    bnb_4bit_quant_type="nf4",              # Тип квантизации NF4 — самый точный и эффективный на 2024–2025 год (лучше fp4)
    bnb_4bit_compute_dtype=torch.float16,   # Во время вычислений внутри модели используем float16 — максимальная скорость на GPU
    bnb_4bit_use_double_quant=True,         # Включаем двойную квантизацию — дополнительно сжимает веса без заметной потери качества
)

Эти две строки загружают токенизатор и саму 8-миллиардную модель **Saiga Llama-3-8B** в сильно сжатом (4-битном) виде, благодаря чему она запускается даже на обычной видеокарте **Colab T4**. После выполнения этого кода у нас в переменной `model` находится полноценный ИИ, способный понимать контекст, помнить диалог и генерировать ответы уровня.

In [7]:
# Загружаем токенизатор (преобразователь текста в токены) для модели Saiga Llama-3-8B
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Загружаем саму нейронную сеть (8 миллиардов параметров) в 4-битном квантизованном виде
# Это основной "мозг" помощника — он генерирует все умные и связные ответы
model = AutoModelForCausalLM.from_pretrained(
    model_name,                              # Откуда брать модель (Hugging Face)
    quantization_config=quantization_config, # Применяем ранее настроенную 4-битную квантизацию (экономия памяти ×4)
    device_map="auto",                       # Автоматически распределяет слои модели по GPU и CPU (если не влезает целиком в VRAM)
    torch_dtype=torch.float16                # Все вычисления внутри модели в половинной точности — быстрее и меньше памяти
)

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/446 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/689 [00:00<?, ?B/s]

model.safetensors.index.json: 0.00B [00:00, ?B/s]

...

model-00002-of-00004.safetensors:   0%|          | 0.00/5.00G [00:00<?, ?B/s]

model-00003-of-00004.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/1.17G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/277 [00:00<?, ?B/s]

В данной части кода загрузим нашу TTS-модель и выполним ее настройку:

In [8]:
# Определяем устройство для TTS-модели: если есть GPU (CUDA) — используем его
device_tts = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Частота дискретизации аудио — 48000 Гц. Silero TTS именно на ней обучена и выдаёт самое лучшее качество звука
sample_rate = 48000

# Загружаем нашу TTS-модель
tts_model, _ = torch.hub.load(repo_or_dir='snakers4/silero-models',
                              model='silero_tts',
                              language='ru',               # Язык — русский
                              speaker='v3_1_ru')           # Версия с самыми качественными голосами

# Переносим модель на выбранное устройство (GPU или CPU) — после этого она готова к генерации речи
tts_model.to(device_tts)

Downloading: "https://github.com/snakers4/silero-models/zipball/master" to /root/.cache/torch/hub/master.zip


100%|██████████| 59.0M/59.0M [00:04<00:00, 13.8MB/s]


Далее зададим системный промпт и запустим историю чата:

In [9]:
system_prompt = """Ты — высокоинтеллектуальный, профессиональный голосовой помощник на русском языке.
Отвечай кратко, точно, по делу, естественно и интересно. Используй только русский язык.
Сохраняй контекст предыдущих сообщений. Если вопрос касается твоих возможностей, перечисли их логично."""

# Инициализируем историю диалога в формате чата Llama-3 (список сообщений с ролями)
# Первый элемент — всегда системный промпт, он будет автоматически подставляться ко всем запросам
# Это основа памяти контекста: дальше будем добавлять сообщения пользователя и помощника
chat_history = [{"role": "system", "content": system_prompt}]

Это основной цикл работы голосового помощника: он бесконечно записывает ваш голос (пока не будет "стоп-слово"), распознаёт речь через **Whisper**, определяет тип запроса (10 команд или свободный диалог), генерирует умный ответ с помощью топовой русской модели `saiga_llama3_8b`, сохраняет контекст и озвучивает ответ максимально естественным голосом **Silero**. Всё работает в реальном времени, с памятью диалога, защитой от плохих ответов и гарантией, что речь никогда не обрывается:

In [11]:
# Сообщаем пользователю, что голосовой ИИ полностью готов к работе
print("Голосовой помощник на saiga_llama3_8b (максимальное качество) запущен!\n")
print("="*60)

import numpy as np

# Основной бесконечный цикл — сердце всего ассистента
while True:
    # Запускаем запись голоса пользователя (8 секунд)
    print("Говорите сейчас (8 секунд)...\n")
    audio_path = record_audio(8)

    # === ИСПРАВЛЕНИЕ БАГА: pydub → чистый numpy-массив 16kHz ===
    print("Распознаю речь...")
    audio = AudioSegment.from_file(audio_path)                    # читаем webm/opus
    audio = audio.set_frame_rate(16000).set_channels(1).set_sample_width(2)  # строго 16 кГц, моно, 16-бит

    # Превращаем в numpy-массив и нормализуем (Whisper ожидает float32 в диапазоне [-1, 1])
    samples = np.array(audio.get_array_of_samples(), dtype=np.float32)
    audio_array = samples / 32768.0                               # нормализация 16-битного сигнала

    # Передаём чистый массив в pipeline — это полностью обходит баг KeyError 'num_frames'
    result = transcriber(
        {"array": audio_array, "sampling_rate": 16000},
        generate_kwargs={
            "language": "russian",
            "task": "transcribe"
        }
    )
    text = result["text"].strip()

    # Если ничего не распознано — просим повторить
    if not text:
        print("Ничего не распознано, попробуйте ещё раз.\n")
        print("="*60)
        continue

    print(f"Вы сказали: {text}\n")
    lower_text = text.lower()
    user_message = text  # По умолчанию — свободный вопрос

    # 10 фиксированных команд — но все ответы идут через мощную модель saiga_llama3_8b
    if any(word in lower_text for word in ["привет", "здравствуй", "добрый день", "доброе утро", "добрый вечер"]):
        user_message = "Приветствие. Ответь вежливо и предложи помощь."
    elif any(word in lower_text for word in ["как дела", "как ты", "как жизнь"]):
        user_message = "Пользователь спрашивает о самочувствии. Ответь позитивно и кратко."
    elif any(phrase in lower_text for phrase in ["что ты умеешь", "функции", "возможности", "что можешь"]):
        user_message = "Опиши свои ключевые возможности: распознавание речи, генерация ответов на основе мощной языковой модели, синтез речи, поддержка контекста диалога."
    elif any(phrase in lower_text for phrase in ["кто ты", "представься", "ты кто"]):
        user_message = "Представься: укажи, что ты ИИ на базе Whisper large-v3 (распознавание), saiga_llama3_8b (генерация), Silero TTS (речь)."
    elif any(word in lower_text for word in ["анекдот", "шутка", "расскажи шутку", "расскажи анекдот"]):
        user_message = "Расскажи короткий, смешной и приличный анекдот на русском."
    elif "переведи на английский" in lower_text:
        phrase = text.split("переведи на английский", 1)[1].strip() if len(text.split("переведи на английский")) > 1 else ""
        user_message = f"Переведи на английский язык следующий текст точно и естественно: {phrase}"
    elif any(word in lower_text for word in ["интересный факт", "факт", "удивительный факт", "расскажи факт"]):
        user_message = "Расскажи один краткий, но захватывающий научный или исторический факт."
    elif any(word in lower_text for word in ["посоветуй книгу", "рекомендуй книгу", "какую книгу почитать"]):
        user_message = "Посоветуй одну хорошую книгу по саморазвитию, науке или психологии с коротким объяснением, почему она стоит внимания."
    elif any(word in lower_text for word in ["спасибо", "благодарю", "спс"]):
        user_message = "Пользователь благодарит. Ответь вежливо и предложи продолжить."
    elif any(word in lower_text for word in ["пока", "до свидания", "выход", "стоп"]):
        response = "До свидания! Было приятно пообщаться. До новых встреч!"
        print(f"Ответ: {response}\n")
        print("="*60)
        audio_tts = tts_model.apply_tts(text=response, speaker='xenia', sample_rate=sample_rate)
        torchaudio.save("response.wav", audio_tts.unsqueeze(0).cpu(), sample_rate, format="wav")
        display(Audio("response.wav", autoplay=True))
        time.sleep(len(AudioSegment.from_wav("response.wav")) / 1000 + 1.2)
        print("Помощник завершил работу.")
        break

    # Генерация ответа через saiga_llama3_8b
    messages = chat_history + [{"role": "user", "content": user_message}]
    input_text = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    inputs = tokenizer(input_text, return_tensors="pt").to(model.device)

    with torch.no_grad():
        generated_ids = model.generate(
            inputs.input_ids,
            max_new_tokens=120,
            temperature=0.75,
            top_p=0.95,
            top_k=50,
            do_sample=True,
            repetition_penalty=1.15,
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.eos_token_id
        )

    response = tokenizer.decode(generated_ids[0][inputs.input_ids.shape[-1]:], skip_special_tokens=True).strip()

    if len(response) < 10 or "не знаю" in response.lower():
        messages[-1]["content"] += " Дай полный и полезный ответ."
        input_text = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
        inputs = tokenizer(input_text, return_tensors="pt").to(model.device)
        generated_ids = model.generate(inputs.input_ids, max_new_tokens=120, temperature=0.7, do_sample=True)
        response = tokenizer.decode(generated_ids[0][inputs.input_ids.shape[-1]:], skip_special_tokens=True).strip()

    # Обновляем историю диалога
    chat_history.append({"role": "user", "content": user_message})
    chat_history.append({"role": "assistant", "content": response})
    if len(chat_history) > 15:
        chat_history = [chat_history[0]] + chat_history[-13:]

    # Выводим и озвучиваем ответ
    print(f"Ответ: {response}\n")
    print("="*60)

    audio = tts_model.apply_tts(text=response, speaker='xenia', sample_rate=sample_rate)
    audio_path_tts = "response.wav"
    torchaudio.save(audio_path_tts, audio.unsqueeze(0).cpu(), sample_rate, format="wav")

    audio_seg = AudioSegment.from_wav(audio_path_tts)
    duration = len(audio_seg) / 1000.0 + 1.0

    display(Audio(audio_path_tts, autoplay=True))
    time.sleep(duration)

Голосовой помощник на saiga_llama3_8b (максимальное качество) запущен!

Говорите сейчас (8 секунд)...



<IPython.core.display.Javascript object>

Распознаю речь...
Вы сказали: Как у тебя дела?

Ответ: Меня часто обновляют и совершенствуют алгоритмы обработки данных, что позволяет мне быть более оперативным и точным в моей работе. Однако моя работа основана на программном обеспечении, поэтому "личное" состояние меня не так важно, как моя способность помогать пользователям. Как могу помочь вам сегодня?



Говорите сейчас (8 секунд)...



<IPython.core.display.Javascript object>

Распознаю речь...
Вы сказали: Кто ты такая?

Ответ: Здравствуйте! Я — искусственный интеллект, состоящий из трех компонентов:
1. **Распознавательная часть:** Базируюсь на модели Whisper Large-V3 для распознания речи.
2. **Генераторная часть:** Оснащён моделью Saige LLaMA 3.8B для генерации текста.
3. **Модуль синтеза речи:** Использую технологии Silero TTS для создания натуральной речи при общении или озв



Говорите сейчас (8 секунд)...



<IPython.core.display.Javascript object>

Распознаю речь...
Вы сказали: Ладно, давай пока.

Ответ: До свидания! Было приятно пообщаться. До новых встреч!



Помощник завершил работу.
